<h1 align=center><font size = 5>Capstone Project - The Battle of Neighborhoods</font></h1>

The objective of this project is to find the most suitable location to establish a cafe/coffee shop in Bangalore, India

In [1]:
pip install geopandas

     |████████████████████████████████| 972kB 4.1MB/s eta 0:00:01
     |████████████████████████████████| 10.9MB 2.8MB/s eta 0:00:01     |████▉                           | 1.6MB 21.4MB/s eta 0:00:01ta 0:00:01
     |████████████████████████████████| 1.8MB 27.7MB/s eta 0:00:01
     |████████████████████████████████| 14.7MB 29.0MB/s eta 0:00:01      | 6.2MB 6.0MB/s eta 0:00:02   | 12.9MB 29.0MB/s eta 0:00:01
  Using cached https://files.pythonhosted.org/packages/d2/3d/fa76db83bf75c4f8d338c2fd15c8d33fdd7ad23a9b5e57eb6c5de26b430e/click-7.1.2-py2.py3-none-any.whl
  Found existing installation: pyproj 1.9.6
    Uninstalling pyproj-1.9.6:
      Successfully uninstalled pyproj-1.9.6
Note: you may need to restart the kernel to use updated packages.


In [2]:
pip install geopy

     |████████████████████████████████| 112kB 10.2MB/s eta 0:00:01
Note: you may need to restart the kernel to use updated packages.


In [3]:
#pip install descartes

In [4]:
#importing necessary libraries
import requests
import pandas as pd
import geopandas as gpd
import numpy as np
from geopy.geocoders import Nominatim
import folium # map rendering library
from sklearn.cluster import KMeans 

In [17]:
#Bengaluru neighbourhoods/wards information is available from the BBMP site
blr_df= gpd.read_file('/resources/labs/DP0701EN/BBMP.GeoJSON')
blr_df.to_csv(r'/resources/labs/DP0701EN/blr_json.csv', index = False)
blr_df.head()

OBJECTID ASS_CONST_  ASS_CONST1  WARD_NO                 WARD_NAME  \
0         1        150   Yelahanka      2.0          Chowdeswari Ward   
1         2        150   Yelahanka      3.0                    Atturu   
2         3        150   Yelahanka      4.0  Yelahanka Satellite Town   
3         4        151  K.R. Puram     51.0               Vijnanapura   
4         5        151  K.R. Puram     53.0              Basavanapura   

     POP_M    POP_F  POP_SC  POP_ST  POP_TOTAL  AREA_SQ_KM        LAT  \
0  10402.0   9224.0  2630.0   286.0    19626.0        7.06  13.121709   
1  13129.0  10891.0  2921.0   665.0    24020.0       10.15  13.102805   
2  13457.0  12325.0  3687.0   601.0    25782.0        4.90  13.090987   
3  18118.0  16969.0  6454.0   228.0    35087.0        2.05  13.006063   
4  11494.0  10518.0  4115.0   325.0    22012.0        6.28  13.016847   

         LON             RESERVATIO  \
0  77.580422                General   
1  77.560038        General (Women)   
2  77.583925  Backward Category - A   
3  77.669565        Scheduled Caste   
4  77.715456                General   

                                            geometry  
0  MULTIPOLYGON (((77.59229 13.09720, 77.59094 13...  
1  MULTIPOLYGON (((77.56862 13.12705, 77.57064 13...  
2  MULTIPOLYGON (((77.59094 13.09842, 77.59229 13...  
3  MULTIPOLYGON (((77.67683 13.01147, 77.67695 13...  
4  MULTIPOLYGON (((77.72899 13.02061, 77.72994 13...

In [18]:
#Retrieve the lat and long for Bangalore
address = 'Bangalore, IN'
geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Bangalore are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Bangalore are 12.9791198, 77.5912997.


In [19]:
# create map of Bangalore using latitude and longitude values
map_blore = folium.Map(location=[latitude, longitude], zoom_start=11)

# Add the color for the chloropleth by population of each ward:
map_blore.choropleth(
 geo_data=blr_df,
 name='choropleth',
 data=blr_df,
 columns=['WARD_NAME', 'POP_TOTAL'],
 key_on='feature.properties.WARD_NAME',
 fill_color='YlGn',
 fill_opacity=0.7,
 line_opacity=0.2,
 legend_name='Population (%)'
)
folium.LayerControl().add_to(map_blore)

# add ward names as markers
for lat, lng, label in zip(blr_df['LAT'], blr_df['LON'], blr_df['WARD_NAME']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=4,
        popup=label,
        color='red',
        fill=True,
        fill_color='yellow',
        fill_opacity=0.5,
        parse_html=False).add_to(map_blore)  
map_blore.save('/resources/labs/DP0701EN/blr_pop.html')
map_blore

In [20]:
CLIENT_ID = '5JFEUYYWAEV54YT0KP2ESZM24MLE5RDHLD0RNORZXQUTANI5' # your Foursquare ID
CLIENT_SECRET = '2IIXNUBF0N4FKEBBM20RYBM4VAB1F1BM2QRHFESRIJO0RTVB' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100
print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 5JFEUYYWAEV54YT0KP2ESZM24MLE5RDHLD0RNORZXQUTANI5
CLIENT_SECRET:2IIXNUBF0N4FKEBBM20RYBM4VAB1F1BM2QRHFESRIJO0RTVB


In [21]:
# function to retrieve all venues for all neighborhoods in Bangalore
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        #print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [22]:
# blr_venues = getNearbyVenues(names=blr_df['WARD_NAME'],
#                                  latitudes=blr_df['LAT'],
#                                   longitudes=blr_df['LON']
#                                 )

In [23]:
#blr_venues.to_csv(r'/resources/labs/DP0701EN/blr_venues.csv', index = False)
blr_venues = pd.read_csv("/resources/labs/DP0701EN/blr_venues.csv")

In [24]:
#No of venues
print(blr_venues.shape)
blr_venues.head()

(1280, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0                    Atturu              13.102805               77.560038   
1                    Atturu              13.102805               77.560038   
2  Yelahanka Satellite Town              13.090987               77.583925   
3  Yelahanka Satellite Town              13.090987               77.583925   
4  Yelahanka Satellite Town              13.090987               77.583925   

                     Venue  Venue Latitude  Venue Longitude     Venue Category  
0            Axis Bank ATM       13.102350        77.560310                ATM  
1            LG Brand Shop       13.102462        77.559921  Electronics Store  
2             Kanti Sweets       13.093498        77.582429       Dessert Shop  
3               Star Daily       13.094401        77.582870     Shopping Plaza  
4  State Bank of India ATM       13.092829        77.587242                ATM

In [25]:
#print out the list of categories
blr_venues['Venue Category'].unique()[:100]

array(['ATM', 'Electronics Store', 'Dessert Shop', 'Shopping Plaza',
       'Pizza Place', 'Indian Restaurant', 'Café', 'Clothing Store',
       'Bus Stop', 'Movie Theater', 'Fast Food Restaurant',
       'American Restaurant', 'Performing Arts Venue',
       'Outdoors & Recreation', 'Soccer Field', 'Recreation Center',
       'Karnataka Restaurant', 'Department Store', 'Pharmacy',
       'Dry Cleaner', 'Fried Chicken Joint', 'Photography Studio',
       'Restaurant', 'Basketball Court', 'Bakery', 'Juice Bar', 'Park',
       'Chinese Restaurant', 'Train Station', 'Coffee Shop',
       'Breakfast Spot', 'Metro Station', 'Resort', 'Indian Sweet Shop',
       'Vegetarian / Vegan Restaurant', 'Indie Movie Theater',
       'Miscellaneous Shop', 'Bar', 'Pool', 'Playground',
       'Ice Cream Shop', 'Food Truck', 'Bus Line', 'Snack Place', 'Pub',
       'Liquor Store', 'Diner', 'Bus Station', 'Burger Joint', 'Gym',
       "Women's Store", 'Gourmet Shop', 'Bookstore', 'Hotel',
       'South In

## Analyze Each Neighborhood/Ward in Bangalore

In [26]:
# one hot encoding
blr_onehot = pd.get_dummies(blr_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
blr_onehot['Neighborhood'] = blr_venues['Neighborhood'] 
#move neighbourhood to first position
col_name="Neighborhood"
first_col = blr_onehot.pop(col_name)
blr_onehot.insert(0,col_name, first_col)
blr_grouped = blr_onehot.groupby('Neighborhood').mean().reset_index()
blr_grouped

Neighborhood   ATM  Airport  American Restaurant  \
0              A Narayanapura  0.00      0.0                  0.0   
1                     Adugodi  0.00      0.0                  0.0   
2                      Agaram  0.00      0.0                  0.0   
3        Agrahara Dasarahalli  0.00      0.0                  0.0   
4                  Anjanapura  0.50      0.0                  0.0   
..                        ...   ...      ...                  ...   
171    Vishwanath Nagenahalli  0.00      0.0                  0.0   
172       Vrisabhavathi Nagar  1.00      0.0                  0.0   
173                   Yediyur  0.00      0.0                  0.0   
174  Yelahanka Satellite Town  0.25      0.0                  0.0   
175             Yeshwanthpura  0.00      0.0                  0.0   

     Andhra Restaurant  Arcade  Art Gallery  Art Museum  Asian Restaurant  \
0                  0.0     0.0          0.0         0.0               0.0   
1                  0.0     0.0          0.0         0.0               0.0   
2                  0.0     0.0          0.0         0.0               0.0   
3                  0.0     0.0          0.0         0.0               0.0   
4                  0.0     0.0          0.0         0.0               0.0   
..                 ...     ...          ...         ...               ...   
171                0.0     0.0          0.0         0.0               0.0   
172                0.0     0.0          0.0         0.0               0.0   
173                0.0     0.0          0.0         0.0               0.0   
174                0.0     0.0          0.0         0.0               0.0   
175                0.0     0.0          0.0         0.0               0.0   

     Athletics & Sports  ...  Theater  Tibetan Restaurant  Trail  \
0                   0.0  ...      0.0                 0.0    0.0   
1                   0.0  ...      0.0                 0.0    0.0   
2                   0.0  ...      0.0                 0.0    0.0   
3                   0.2  ...      0.0                 0.0    0.0   
4                   0.0  ...      0.0                 0.0    0.0   
..                  ...  ...      ...                 ...    ...   
171                 0.0  ...      0.0                 0.0    0.0   
172                 0.0  ...      0.0                 0.0    0.0   
173                 0.0  ...      0.0                 0.0    0.0   
174                 0.0  ...      0.0                 0.0    0.0   
175                 0.0  ...      0.0                 0.0    0.0   

     Train Station  Turkish Restaurant  Vegetarian / Vegan Restaurant  \
0              0.0                 0.0                            0.0   
1              0.0                 0.0                            0.0   
2              0.0                 0.0                            0.0   
3              0.0                 0.0                            0.0   
4              0.0                 0.0                            0.0   
..             ...                 ...                            ...   
171            0.0                 0.0                            0.0   
172            0.0                 0.0                            0.0   
173            0.0                 0.0                            0.0   
174            0.0                 0.0                            0.0   
175            0.5                 0.0                            0.0   

     Vietnamese Restaurant  Wine Shop  Women's Store  Yoga Studio  
0                      0.0        0.0            0.0          0.0  
1                      0.0        0.0            0.0          0.0  
2                      0.0        0.0            0.0          0.0  
3                      0.0        0.0            0.0          0.0  
4                      0.0        0.0            0.0          0.0  
..                     ...        ...            ...          ...  
171                    0.0        0.0            0.0          0.0  
172                    0.

In [27]:
#function to sort the venues in descending order.
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [28]:
# Retrive the top 10 venues in each ward
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = blr_grouped['Neighborhood']

for ind in np.arange(blr_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(blr_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0        A Narayanapura     Electronics Store         Movie Theater   
1               Adugodi                  Café     Indian Restaurant   
2                Agaram          Burger Joint           Yoga Studio   
3  Agrahara Dasarahalli     Indian Restaurant     Electronics Store   
4            Anjanapura                   ATM            Campground   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0              Bus Stop           Yoga Studio           Dry Cleaner   
1            Donut Shop                  Food           Flea Market   
2           Dry Cleaner                  Food           Flea Market   
3    Athletics & Sports                  Café            Bagel Shop   
4            Donut Shop                  Food           Flea Market   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Flea Market  Fast Food Restaurant        Farmers Market   
1  Fast Food Restaurant        Farmers Market           Event Space   
2  Fast Food Restaurant        Farmers Market           Event Space   
3           Yoga Studio           Dry Cleaner                  Food   
4  Fast Food Restaurant        Farmers Market           Event Space   

  9th Most Common Venue       10th Most Common Venue  
0           Event Space  Eastern European Restaurant  
1     Electronics Store  Eastern European Restaurant  
2     Electronics Store  Eastern European Restaurant  
3           Flea Market         Fast Food Restaurant  
4     Electronics Store  Eastern European Restaurant

In [30]:
to_grouped = blr_onehot.groupby(["Neighborhood"]).mean().reset_index()
to_grouped.head()

Neighborhood  ATM  Airport  American Restaurant  Andhra Restaurant  \
0        A Narayanapura  0.0      0.0                  0.0                0.0   
1               Adugodi  0.0      0.0                  0.0                0.0   
2                Agaram  0.0      0.0                  0.0                0.0   
3  Agrahara Dasarahalli  0.0      0.0                  0.0                0.0   
4            Anjanapura  0.5      0.0                  0.0                0.0   

   Arcade  Art Gallery  Art Museum  Asian Restaurant  Athletics & Sports  ...  \
0     0.0          0.0         0.0               0.0                 0.0  ...   
1     0.0          0.0         0.0               0.0                 0.0  ...   
2     0.0          0.0         0.0               0.0                 0.0  ...   
3     0.0          0.0         0.0               0.0                 0.2  ...   
4     0.0          0.0         0.0               0.0                 0.0  ...   

   Theater  Tibetan Restaurant  Trail  Train Station  Turkish Restaurant  \
0      0.0                 0.0    0.0            0.0                 0.0   
1      0.0                 0.0    0.0            0.0                 0.0   
2      0.0                 0.0    0.0            0.0                 0.0   
3      0.0                 0.0    0.0            0.0                 0.0   
4      0.0                 0.0    0.0            0.0                 0.0   

   Vegetarian / Vegan Restaurant  Vietnamese Restaurant  Wine Shop  \
0                            0.0                    0.0        0.0   
1                            0.0                    0.0        0.0   
2                            0.0                    0.0        0.0   
3                            0.0                    0.0        0.0   
4                            0.0                    0.0        0.0   

   Women's Store  Yoga Studio  
0            0.0          0.0  
1            0.0          0.0  
2            0.0          0.0  
3            0.0          0.0  
4            0.0          0.0  

[5 rows x 186 columns]

In [31]:
#Create a new dataframe to find Cafes only
cafe_df = to_grouped[["Neighborhood","Café", "Coffee Shop"]].copy()
cafe_df.sort_values(by=['Café', 'Coffee Shop'], inplace=True,ascending=False)
cafe_df.head()

Neighborhood      Café  Coffee Shop
126    Prakash Nagar  0.666667          0.0
1            Adugodi  0.500000          0.0
93      Kottegepalya  0.500000          0.0
135  Ramaswamy Palya  0.500000          0.0
142   Sarvagna Nagar  0.500000          0.0

## Cluster Neighborhoods

In [32]:
# set number of clusters
toclusters = 4
to_clustering = cafe_df.drop(["Neighborhood"], 1)
# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=0).fit(to_clustering)
# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20]

array([3, 3, 3, 3, 3, 2, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1],
      dtype=int32)

In [33]:
# create a new dataframe that includes the cluster as well as the labels
to_merged = cafe_df.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged

Neighborhood      Café  Coffee Shop  Cluster Labels
126             Prakash Nagar  0.666667          0.0               3
1                     Adugodi  0.500000          0.0               3
93               Kottegepalya  0.500000          0.0               3
135           Ramaswamy Palya  0.500000          0.0               3
142            Sarvagna Nagar  0.500000          0.0               3
..                        ...       ...          ...             ...
171    Vishwanath Nagenahalli  0.000000          0.0               0
172       Vrisabhavathi Nagar  0.000000          0.0               0
173                   Yediyur  0.000000          0.0               0
174  Yelahanka Satellite Town  0.000000          0.0               0
175             Yeshwanthpura  0.000000          0.0               0

[176 rows x 4 columns]

In [34]:
# merge blr_grouped with blr_data to add latitude/longitude for each neighborhood
to_merged = to_merged.join(blr_venues.set_index("Neighborhood"), on="Neighborhood")
print(to_merged.shape)
to_merged.head()

(1280, 10)


Neighborhood      Café  Coffee Shop  Cluster Labels  \
126  Prakash Nagar  0.666667          0.0               3   
126  Prakash Nagar  0.666667          0.0               3   
126  Prakash Nagar  0.666667          0.0               3   
1          Adugodi  0.500000          0.0               3   
1          Adugodi  0.500000          0.0               3   

     Neighborhood Latitude  Neighborhood Longitude               Venue  \
126              12.993094               77.558221  O.G. Variar & Sons   
126              12.993094               77.558221     Cafe Coffee Day   
126              12.993094               77.558221     Cafe Coffee Day   
1                12.943239               77.613079             Bayleaf   
1                12.943239               77.613079                 CCD   

     Venue Latitude  Venue Longitude     Venue Category  
126       12.991578        77.554561             Bakery  
126       12.989818        77.559464               Café  
126       12.995895        77.554804               Café  
1         12.940480        77.616640  Indian Restaurant  
1         12.945474        77.610923               Café

In [35]:
# sort the results by Cluster Labels
print(to_merged.shape)
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged

(1280, 10)


Neighborhood      Café  Coffee Shop  Cluster Labels  \
7          Attiguppe  0.066667          0.0               0   
27        Cottonpete  0.000000          0.0               0   
27        Cottonpete  0.000000          0.0               0   
27        Cottonpete  0.000000          0.0               0   
25         Chickpete  0.000000          0.0               0   
..               ...       ...          ...             ...   
135  Ramaswamy Palya  0.500000          0.0               3   
135  Ramaswamy Palya  0.500000          0.0               3   
142   Sarvagna Nagar  0.500000          0.0               3   
93      Kottegepalya  0.500000          0.0               3   
126    Prakash Nagar  0.666667          0.0               3   

     Neighborhood Latitude  Neighborhood Longitude  \
7                12.958112               77.529309   
27               12.970359               77.566287   
27               12.970359               77.566287   
27               12.970359               77.566287   
25               12.970688               77.577098   
..                     ...                     ...   
135              13.005976               77.599077   
135              13.005976               77.599077   
142              12.989170               77.631039   
93               12.982456               77.514090   
126              12.993094               77.558221   

                              Venue  Venue Latitude  Venue Longitude  \
7               village hypermarket       12.961129        77.526633   
27       Govinda Rao Military Hotel       12.968805        77.570220   
27                       Cotton Pet       12.971385        77.570234   
27                              KFC       12.974282        77.566137   
25               Sachin Light House       12.972864        77.573201   
..                              ...             ...              ...   
135                 Cafe Coffee Day       13.003135        77.596594   
135      Airtel Relationship Center       13.001860        77.598961   
142  Army Service Corps Golf Course       12.991714        77.633899   
93              Coffee Day Drive In       12.980420        77.510398   
126              O.G. Variar & Sons       12.991578        77.554561   

           Venue Category  
7          Farmers Market  
27                  Hotel  
27              Rest Area  
27   Fast Food Restaurant  
25     Miscellaneous Shop  
..                    ...  
135                  Café  
135     Electronics Store  
142           Golf Course  
93                   Café  
126                Bakery  

[1280 rows x 10 columns]

In [40]:
# create map of Bangalore using latitude and longitude values
map_blore = folium.Map(location=[latitude, longitude], zoom_start=11)

# Add the color for the chloropleth by population of each ward:
map_blore.choropleth(
 geo_data=blr_df,
 name='choropleth',
 data=blr_df,
 columns=['WARD_NAME', 'POP_TOTAL'],
 key_on='feature.properties.WARD_NAME',
 fill_color='YlGn',
 fill_opacity=0.7,
 line_opacity=0.2,
 legend_name='Population (%)'
)
folium.LayerControl().add_to(map_blore)

# set color scheme for the clusters
x = np.arange(toclusters)
ys = [i+x+(i*x)**2 for i in range(toclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

colordict = {-1: 'purple', 0: 'blue', 1: 'orange', 2: 'red'}
# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Neighborhood'], to_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster))
    folium.CircleMarker(
        [lat, lon],
        radius=3,
        popup=label,
        color=colordict[cluster-1],
        fill_color=colordict[cluster-1], fill=True,
        fill_opacity=1).add_to(map_blore)
map_blore.save('/resources/labs/DP0701EN/blr_cafe_segments.html')       
map_blore

## Examine Clusters

#### Cluster 1

In [58]:
fullcluster0 = to_merged.loc[to_merged['Cluster Labels'] == 0].copy()
clustertemp0 = fullcluster0[["Neighborhood", "Cluster Labels"]].copy()
clustertemp0.drop_duplicates(inplace=True) 
cluster0 = pd.merge(clustertemp0,neighborhoods_venues_sorted, on='Neighborhood')
cluster0

Neighborhood  Cluster Labels  1st Most Common Venue  \
0               Sarakki               0      Indian Restaurant   
1      Deepanjali Nagar               0               Tea Room   
2       Dayananda Nagar               0  Performing Arts Venue   
3            Cottonpete               0                  Hotel   
4             Chickpete               0      Indian Restaurant   
..                  ...             ...                    ...   
121   Govindaraja Nagar               0      Indian Restaurant   
122        Rajaji Nagar               0      Indian Restaurant   
123  Vishveshwara Puram               0   Fast Food Restaurant   
124          BTM Layout               0      Indian Restaurant   
125   Dattatreya Temple               0      Indian Restaurant   

             2nd Most Common Venue    3rd Most Common Venue  \
0                      Snack Place     Fast Food Restaurant   
1                            Hotel           Breakfast Spot   
2                            Plaza                Multiplex   
3             Fast Food Restaurant              Yoga Studio   
4                            Plaza  South Indian Restaurant   
..                             ...                      ...   
121                    Bus Station              Snack Place   
122                           Park       Chinese Restaurant   
123                           Park                   Bakery   
124                    Snack Place                   Bakery   
125  Vegetarian / Vegan Restaurant                     Café   

    4th Most Common Venue          5th Most Common Venue  \
0        Department Store                            Pub   
1              Donut Shop                           Food   
2                 Dog Run                    Flea Market   
3              Donut Shop                           Food   
4      Miscellaneous Shop            Arts & Crafts Store   
..                    ...                            ...   
121            Bagel Shop                 Breakfast Spot   
122    Seafood Restaurant  Vegetarian / Vegan Restaurant   
123          Dessert Shop                           Café   
124  Fast Food Restaurant                    Coffee Shop   
125           Snack Place                     Restaurant   

             6th Most Common Venue 7th Most Common Venue  \
0                             Café     Electronics Store   
1                      Flea Market  Fast Food Restaurant   
2             Fast Food Restaurant           Event Space   
3                      Flea Market           Event Space   
4                       Restaurant            Donut Shop   
..                             ...                   ...   
121  Vegetarian / Vegan Restaurant                Bakery   
122           Fast Food Restaurant         Grocery Store   
123                     Restaurant         Metro Station   
124  Vegetarian / Vegan Restaurant        Ice Cream Shop   
125                    Pizza Place                   Bar   

    8th Most Common Venue        9th Most Common Venue  \
0      Chinese Restaurant        Hyderabadi Restaurant   
1             Event Space            Electronics Store   
2       Electronics Store  Eastern European Restaurant   
3       Electronics Store  Eastern European Restaurant   
4    Fast Food Restaurant                  Event Space   
..                    ...                          ...   
121                  Café                  Yoga Studio   
122                  Café                      Dog Run   
123           Snack Place                   Food Truck   
124    Chinese Restaurant                         Café   
125  Karnataka Restaurant                   Donut Shop   

          10th Most Common Venue  
0              Andhra Restaurant  
1    Eastern European Restaurant  
2            Dumpling Restaurant  
3            Dumpling Restaurant  
4              Electronics Store  
..                           ...  
121                         Food  
122                  Event Space  
123    

#### Cluster 2

In [59]:
fullcluster1 = to_merged.loc[to_merged['Cluster Labels'] == 1].copy()
clustertemp1 = fullcluster1[["Neighborhood", "Cluster Labels"]].copy()
clustertemp1.drop_duplicates(inplace=True) 
cluster1 = pd.merge(clustertemp1,neighborhoods_venues_sorted, on='Neighborhood')
cluster1

Neighborhood  Cluster Labels 1st Most Common Venue  \
0             Shantala Nagar               1                  Café   
1           Subramanya Nagar               1                  Café   
2                    Hagadur               1               Brewery   
3                  Jayamahal               1     Indian Restaurant   
4              Sagayarapuram               1                  Park   
5                     Domlur               1                  Café   
6                  J P Nagar               1     Indian Restaurant   
7                Koramangala               1                  Café   
8                  Jogupalya               1     Indian Restaurant   
9                Mudalapalya               1           Bus Station   
10               Malleswaram               1     Indian Restaurant   
11              Kottegepalya               1                  Café   
12                Konankunte               1                  Café   
13  Banashankari Temple ward               1         Metro Station   
14                Azad Nagar               1         Shopping Mall   
15             Chikkalsandra               1           Men's Store   
16               Ganga Nagar               1                  Café   
17             Shanthi Nagar               1     Convenience Store   
18                Bellanduru               1              Tea Room   
19           Vidyapeeta ward               1         Shopping Mall   
20                   Kengeri               1              Pharmacy   
21        Kumaraswamy Layout               1                  Café   

   2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0      Indian Restaurant                   Pub                 Hotel   
1              Multiplex           Supermarket    Chinese Restaurant   
2                   Café                 Hotel     Kerala Restaurant   
3                   Café           Event Space                Bakery   
4         Ice Cream Shop      Department Store    Chinese Restaurant   
5      Indian Restaurant    Chinese Restaurant    Italian Restaurant   
6                   Café                 Diner  Fast Food Restaurant   
7      Indian Restaurant           Coffee Shop                   Pub   
8            Candy Store                  Café    Chinese Restaurant   
9              Nightclub                  Café           Supermarket   
10             Juice Bar                  Café           Yoga Studio   
11     Indian Restaurant        Breakfast Spot                  Park   
12        Breakfast Spot     Indian Restaurant         Grocery Store   
13        Sandwich Place                Bakery                  Café   
14  Fast Food Restaurant                  Café             Multiplex   
15        Clothing Store           Pizza Place   Sporting Goods Shop   
16         Garden Center       Motorcycle Shop           Flea Market   
17                 Hotel     Indian Restaurant                  Café   
18     Indian Restaurant                  Café        Sandwich Place   
19  Fast Food Restaurant                  Café                  Park   
20     Indian Restaurant         Movie Theater           Dry Cleaner   
21            Food Truck        Breakfast Spot        Ice Cream Shop   

      5th Most Common Venue        6th Most Common Venue  \
0                   Brewery                          Gym   
1                Food Court                Movie Theater   
2                 Hotel Bar  Eastern European Restaurant   
3               Music Venue                   Donut Shop   
4                    Bakery                         Café   
5     Rajasthani Restaurant               Sandwich Place   
6   South Indian Restaurant                    Juice Bar   
7            Ice Cream Shop                  Pizza Place   
8        Athletics & Sports                         Food   
9               Yoga Studio                  Flea Market   
10               Donut Shop                         Food   
11             Dance Studio 

#### Cluster 3

In [60]:
fullcluster2 = to_merged.loc[to_merged['Cluster Labels'] == 2].copy()
clustertemp2 = fullcluster2[["Neighborhood", "Cluster Labels"]].copy()
clustertemp2.drop_duplicates(inplace=True) 
cluster2 = pd.merge(clustertemp2,neighborhoods_venues_sorted, on='Neighborhood')
cluster2

Neighborhood  Cluster Labels 1st Most Common Venue  \
0       Ramaswamy Palya               2            Food Truck   
1               Adugodi               2                  Café   
2         Prakash Nagar               2                  Café   
3                  Hudi               2                  Café   
4        Sarvagna Nagar               2           Golf Course   
5  Rajarajeshwari Nagar               2                Bakery   
6  Agrahara Dasarahalli               2                  Café   

  2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
0                  Café            Donut Shop                  Food   
1     Indian Restaurant            Donut Shop     Food & Drink Shop   
2       Motorcycle Shop                Bakery           Dry Cleaner   
3     Indian Restaurant           Pizza Place    Tibetan Restaurant   
4                  Café               Dog Run                  Food   
5                  Café      Department Store           Yoga Studio   
6     Indian Restaurant            Bagel Shop           Dry Cleaner   

  5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
0           Flea Market  Fast Food Restaurant           Event Space   
1                  Food           Flea Market  Fast Food Restaurant   
2                  Food           Flea Market  Fast Food Restaurant   
3           Yoga Studio               Dog Run           Flea Market   
4           Flea Market  Fast Food Restaurant           Event Space   
5   Dumpling Restaurant     Food & Drink Shop                  Food   
6     Food & Drink Shop                  Food           Flea Market   

  8th Most Common Venue        9th Most Common Venue  \
0     Electronics Store  Eastern European Restaurant   
1           Event Space            Electronics Store   
2           Event Space            Electronics Store   
3  Fast Food Restaurant                  Event Space   
4     Electronics Store  Eastern European Restaurant   
5           Flea Market         Fast Food Restaurant   
6  Fast Food Restaurant                  Event Space   

        10th Most Common Venue  
0          Dumpling Restaurant  
1  Eastern European Restaurant  
2  Eastern European Restaurant  
3            Electronics Store  
4          Dumpling Restaurant  
5                  Event Space  
6            Electronics Store

#### Cluster 4

In [61]:
fullcluster3 = to_merged.loc[to_merged['Cluster Labels'] == 3].copy()
clustertemp3 = fullcluster3[["Neighborhood", "Cluster Labels"]].copy()
clustertemp3.drop_duplicates(inplace=True) 
cluster3 = pd.merge(clustertemp3,neighborhoods_venues_sorted, on='Neighborhood')
cluster3

Neighborhood  Cluster Labels 1st Most Common Venue  \
0      Hombegowda Nagara               3     Indian Restaurant   
1           Marathahalli               3              Tea Room   
2         Chalavadipalya               3         Shopping Mall   
3           Sunkenahalli               3     Indian Restaurant   
4   Kadu Malleshwar Ward               3     Indian Restaurant   
5               Srinagar               3  Fast Food Restaurant   
6        Konena Agrahara               3     Indian Restaurant   
7         Dodda Nekkundi               3        Ice Cream Shop   
8             HBR Layout               3           Coffee Shop   
9       New Tippasandara               3                  Park   
10              HMT Ward               3           Coffee Shop   
11      Padmanabha Nagar               3           Coffee Shop   
12    Maruthi Seva Nagar               3  Fast Food Restaurant   
13       C V Raman Nagar               3     Indian Restaurant   
14       Kacharkanahalli               3           Coffee Shop   
15               Halsoor               3     Indian Restaurant   

            2nd Most Common Venue          3rd Most Common Venue  \
0            Karnataka Restaurant                    Coffee Shop   
1                     Coffee Shop             Mexican Restaurant   
2                     Coffee Shop  Vegetarian / Vegan Restaurant   
3                     Coffee Shop                 Ice Cream Shop   
4   Vegetarian / Vegan Restaurant                    Coffee Shop   
5                     Coffee Shop                           Café   
6                       Juice Bar                     Restaurant   
7                     Coffee Shop              Indian Restaurant   
8                            Road                  Jewelry Store   
9                     Coffee Shop                     Food Truck   
10              Indian Restaurant                  Train Station   
11               Toy / Game Store                           Pool   
12                  Shopping Mall                    Coffee Shop   
13                    Pizza Place                           Park   
14                    Snack Place           Fast Food Restaurant   
15                    Coffee Shop            Sporting Goods Shop   

              4th Most Common Venue     5th Most Common Venue  \
0   Southern / Soul Food Restaurant               Bus Station   
1                 Indian Restaurant      Fast Food Restaurant   
2                     Big Box Store          Department Store   
3              Fast Food Restaurant            Sandwich Place   
4                    Ice Cream Shop               Flea Market   
5                       Yoga Studio                Donut Shop   
6                 Korean Restaurant                      Café   
7                       Yoga Studio                Donut Shop   
8                       Bus Station               Yoga Studio   
9                    Sandwich Place                Donut Shop   
10             Fast Food Restaurant          Department Store   
11                             Café             Deli / Bodega   
12                 Department Store            Clothing Store   
13                      Coffee Shop          Department Store   
14          South Indian Restaurant        Chinese Restaurant   
15                             Café  Mediterranean Restaurant   

             6th Most Common Venue 7th Most Common Venue  \
0                             Café           Dry Cleaner   
1   Multicuisine Indian Restaurant            Donut Shop   
2                        Multiplex   Sporting Goods Shop   
3                 Department Store           Pizza Place   
4                      Snack Place            Donut Shop   
5                             Food           Flea Market   
6                      Pizza Place        Breakfast Spot   
7                             Food           Flea Market   
8                      Dry Cleaner           Flea Market   
9                      Fle